In [9]:
import os
import zipfile

# Function to extract ZIP files recursively
def extract_all_zip_files(zip_file_path, extract_to):
    print(f"Extracting {zip_file_path} to {extract_to}")
    with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
        zip_ref.extractall(extract_to)

    # Check for nested zip files and extract them
    for root, dirs, files in os.walk(extract_to):
        for file in files:
            file_path = os.path.join(root, file)
            if zipfile.is_zipfile(file_path):
                new_extract_to = os.path.join(root, os.path.splitext(file)[0])
                os.makedirs(new_extract_to, exist_ok=True)
                extract_all_zip_files(file_path, new_extract_to)

# Paths
first_zip_path = '../202405.zip'
extracted_path = '../data/raw'


# Start the extraction process
extract_all_zip_files(first_zip_path, extracted_path)


Extracting ../202405.zip to ../data/raw
Extracting ../data/raw/202405/20240503.zip to ../data/raw/202405/20240503
Extracting ../data/raw/202405/20240502.zip to ../data/raw/202405/20240502
Extracting ../data/raw/202405/20240501.zip to ../data/raw/202405/20240501
Extracting ../data/raw/202405/20240505.zip to ../data/raw/202405/20240505
Extracting ../data/raw/202405/20240504.zip to ../data/raw/202405/20240504


In [11]:

# Function to determine table name using startswith
def get_table_name(parquet_file_name):
    if parquet_file_name.startswith('event'):
        return 'MatchEventInfo'
    elif parquet_file_name.startswith('pbp'):
        return 'PeriodInfo'
    elif parquet_file_name.startswith('votes'):
        return 'MatchVotesInfo'
    elif parquet_file_name.startswith('tournament'):
        return 'MatchTournamentInfo'
    elif parquet_file_name.startswith('season'):
        return 'MatchSeasonInfo'
    elif parquet_file_name.startswith('round'):
        return 'MatchRoundInfo'
    elif parquet_file_name.startswith('venue'):
        return 'MatchVenueInfo'
    elif parquet_file_name.startswith('home_team'):
        return 'MatchHomeTeamInfo'
    elif parquet_file_name.startswith('away_team'):
        return 'MatchAwayTeamInfo'
    elif parquet_file_name.startswith('home_team_score'):
        return 'MatchHomeScoreInfo'
    elif parquet_file_name.startswith('away_team_score'):
        return 'MatchAwayScoreInfo'
    elif parquet_file_name.startswith('time'):
        return 'MatchTimeInfo'
    elif parquet_file_name.startswith('statistics'):
        return 'GameInfo'
    elif parquet_file_name.startswith('odds'):
        return 'OddsInfo'
    elif parquet_file_name.startswith('power'):
        return 'PowerInfo'
    else:
        return None

# Create empty DataFrames for each schema
data_frames = {
    'MatchEventInfo': pd.DataFrame(),
    'PeriodInfo': pd.DataFrame(),
    'MatchVotesInfo': pd.DataFrame(),
    'MatchTournamentInfo': pd.DataFrame(),
    'MatchSeasonInfo': pd.DataFrame(),
    'MatchRoundInfo': pd.DataFrame(),
    'MatchVenueInfo': pd.DataFrame(),
    'MatchHomeTeamInfo': pd.DataFrame(),
    'MatchAwayTeamInfo': pd.DataFrame(),
    'MatchHomeScoreInfo': pd.DataFrame(),
    'MatchAwayScoreInfo': pd.DataFrame(),
    'MatchTimeInfo': pd.DataFrame(),
    'GameInfo': pd.DataFrame(),
    'OddsInfo': pd.DataFrame(),
    'PowerInfo': pd.DataFrame()
}

# Step 3: Read Parquet files and concatenate into DataFrames
for root, dirs, files in os.walk(extracted_path):
    for file in files:
        if file.endswith('.parquet'):
            parquet_file_path = os.path.join(root, file)
            parquet_file_name = os.path.basename(parquet_file_path)
            table_name = get_table_name(parquet_file_name)
            if table_name:
                print(f"Reading {parquet_file_path} into {table_name} DataFrame")
                df = pd.read_parquet(parquet_file_path)
                if df.empty:
                    print(f"Warning: {parquet_file_path} is empty.")
                print(f"Before concatenation: {table_name} DataFrame shape: {data_frames[table_name].shape}")
                data_frames[table_name] = pd.concat([data_frames[table_name], df], ignore_index=True)
                print(f"After concatenation: {table_name} DataFrame shape: {data_frames[table_name].shape}")
            else:
                print(f"No table mapping found for {parquet_file_name}")

output_dir = '../data/processed'

# Step 4: Export DataFrames to CSV files
for table_name, df in data_frames.items():
    file_path = os.path.join(output_dir, f"{table_name}.csv")
    df.to_csv(file_path, index=False)
    print(f"Saved {file_path} with shape: {df.shape}")


Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/event_12276860.parquet into MatchEventInfo DataFrame
Before concatenation: MatchEventInfo DataFrame shape: (0, 0)
After concatenation: MatchEventInfo DataFrame shape: (1, 10)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/round_12298547.parquet into MatchRoundInfo DataFrame
Before concatenation: MatchRoundInfo DataFrame shape: (0, 0)
After concatenation: MatchRoundInfo DataFrame shape: (1, 5)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/time_12303632.parquet into MatchTimeInfo DataFrame
Before concatenation: MatchTimeInfo DataFrame shape: (0, 0)
After concatenation: MatchTimeInfo DataFrame shape: (1, 7)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/event_12296111.parquet into MatchEventInfo DataFrame
Before concatenation: MatchEventInfo DataFrame shape: (1, 10)
After concatenation: MatchEventInfo DataFrame shape: (2, 10)
Reading ../data/raw/202405/20240503/data/raw/raw_matc

Before concatenation: MatchHomeTeamInfo DataFrame shape: (5, 31)
After concatenation: MatchHomeTeamInfo DataFrame shape: (6, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/away_team_12276832.parquet into MatchAwayTeamInfo DataFrame
Before concatenation: MatchAwayTeamInfo DataFrame shape: (5, 31)
After concatenation: MatchAwayTeamInfo DataFrame shape: (6, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/home_team_12276841.parquet into MatchHomeTeamInfo DataFrame
Before concatenation: MatchHomeTeamInfo DataFrame shape: (6, 31)
After concatenation: MatchHomeTeamInfo DataFrame shape: (7, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/away_team_12300112.parquet into MatchAwayTeamInfo DataFrame
Before concatenation: MatchAwayTeamInfo DataFrame shape: (6, 31)
After concatenation: MatchAwayTeamInfo DataFrame shape: (7, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/tournament_12298585.parquet into MatchTournamentInfo

Before concatenation: MatchEventInfo DataFrame shape: (8, 10)
After concatenation: MatchEventInfo DataFrame shape: (9, 10)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/home_team_score_12298441.parquet into MatchHomeTeamInfo DataFrame
Before concatenation: MatchHomeTeamInfo DataFrame shape: (17, 31)
After concatenation: MatchHomeTeamInfo DataFrame shape: (18, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/round_12299952.parquet into MatchRoundInfo DataFrame
Before concatenation: MatchRoundInfo DataFrame shape: (5, 5)
After concatenation: MatchRoundInfo DataFrame shape: (6, 5)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/away_team_12298795.parquet into MatchAwayTeamInfo DataFrame
Before concatenation: MatchAwayTeamInfo DataFrame shape: (19, 31)
After concatenation: MatchAwayTeamInfo DataFrame shape: (20, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/away_team_12300610.parquet into MatchAwayTeamInfo DataFrame
Bef

Before concatenation: MatchSeasonInfo DataFrame shape: (14, 4)
After concatenation: MatchSeasonInfo DataFrame shape: (15, 4)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/tournament_12302913.parquet into MatchTournamentInfo DataFrame
Before concatenation: MatchTournamentInfo DataFrame shape: (14, 16)
After concatenation: MatchTournamentInfo DataFrame shape: (15, 16)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/home_team_score_12298718.parquet into MatchHomeTeamInfo DataFrame
Before concatenation: MatchHomeTeamInfo DataFrame shape: (31, 31)
After concatenation: MatchHomeTeamInfo DataFrame shape: (32, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/away_team_score_12301127.parquet into MatchAwayTeamInfo DataFrame
Before concatenation: MatchAwayTeamInfo DataFrame shape: (32, 31)
After concatenation: MatchAwayTeamInfo DataFrame shape: (33, 31)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/venue_12303632.parquet into Mat

Before concatenation: MatchRoundInfo DataFrame shape: (22, 5)
After concatenation: MatchRoundInfo DataFrame shape: (23, 5)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/time_12276930.parquet into MatchTimeInfo DataFrame
Before concatenation: MatchTimeInfo DataFrame shape: (21, 7)
After concatenation: MatchTimeInfo DataFrame shape: (22, 7)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/time_12276858.parquet into MatchTimeInfo DataFrame
Before concatenation: MatchTimeInfo DataFrame shape: (22, 7)
After concatenation: MatchTimeInfo DataFrame shape: (23, 7)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/round_12261531.parquet into MatchRoundInfo DataFrame
Before concatenation: MatchRoundInfo DataFrame shape: (23, 5)
After concatenation: MatchRoundInfo DataFrame shape: (24, 5)
Reading ../data/raw/202405/20240503/data/raw/raw_match_parquet/time_12300999.parquet into MatchTimeInfo DataFrame
Before concatenation: MatchTimeInfo DataFrame shape: (

...

Before concatenation: GameInfo DataFrame shape: (99251, 13)
After concatenation: GameInfo DataFrame shape: (99305, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12294068.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (99305, 13)
After concatenation: GameInfo DataFrame shape: (99359, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12293465.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (99359, 13)
After concatenation: GameInfo DataFrame shape: (99413, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12293475.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (99413, 13)
After concatenation: GameInfo DataFrame shape: (99467, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12295614.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame sha

After concatenation: GameInfo DataFrame shape: (101262, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12293506.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (101262, 13)
After concatenation: GameInfo DataFrame shape: (101316, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12276927.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (101316, 13)
After concatenation: GameInfo DataFrame shape: (101370, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12276937.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (101370, 13)
After concatenation: GameInfo DataFrame shape: (101424, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12276783.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (101424, 13)
After concatenation: GameInfo DataFr

Before concatenation: GameInfo DataFrame shape: (103298, 13)
After concatenation: GameInfo DataFrame shape: (103352, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12297924.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (103352, 13)
After concatenation: GameInfo DataFrame shape: (103369, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12291489.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (103369, 13)
After concatenation: GameInfo DataFrame shape: (103440, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12292485.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (103440, 13)
After concatenation: GameInfo DataFrame shape: (103492, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12298150.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataF

Before concatenation: GameInfo DataFrame shape: (105728, 13)
After concatenation: GameInfo DataFrame shape: (105781, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12291498.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (105781, 13)
After concatenation: GameInfo DataFrame shape: (105835, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12292946.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (105835, 13)
After concatenation: GameInfo DataFrame shape: (105889, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12291832.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataFrame shape: (105889, 13)
After concatenation: GameInfo DataFrame shape: (105943, 13)
Reading ../data/raw/202405/20240501/data/raw/raw_statistics_parquet/statistics_12298151.parquet into GameInfo DataFrame
Before concatenation: GameInfo DataF

After concatenation: GameInfo DataFrame shape: (107899, 13)
Saved ../data/processed/MatchEventInfo.csv with shape: (2726, 10)
Saved ../data/processed/PeriodInfo.csv with shape: (205989, 13)
Saved ../data/processed/MatchVotesInfo.csv with shape: (2726, 3)
Saved ../data/processed/MatchTournamentInfo.csv with shape: (2726, 16)
Saved ../data/processed/MatchSeasonInfo.csv with shape: (2726, 4)
Saved ../data/processed/MatchRoundInfo.csv with shape: (1697, 5)
Saved ../data/processed/MatchVenueInfo.csv with shape: (2710, 5)
Saved ../data/processed/MatchHomeTeamInfo.csv with shape: (4566, 31)
Saved ../data/processed/MatchAwayTeamInfo.csv with shape: (4514, 31)
Saved ../data/processed/MatchHomeScoreInfo.csv with shape: (0, 0)
Saved ../data/processed/MatchAwayScoreInfo.csv with shape: (0, 0)
Saved ../data/processed/MatchTimeInfo.csv with shape: (2726, 7)
Saved ../data/processed/GameInfo.csv with shape: (107899, 13)
Saved ../data/processed/OddsInfo.csv with shape: (4394, 11)
Saved ../data/processe